In [16]:
import json
import logging
import sys

import cvxportfolio as cp
import pandas as pd

from clsa_te.data_loader import query_universe, query_ret
from clsa_te.optimizer import Optimizer
from clsa_te.position_loader import PositionsLoader
from clsa_te.trade_engine import TradeEngine

pd.options.plotting.backend = "plotly"

In [3]:
# setup logger
logging.basicConfig()
logging.getLogger().setLevel(logging.INFO)

In [5]:
# read config and define run_date
run_date = pd.Timestamp(2022, 5, 26)
cfg = json.load(open('cfg/JW_SP100.json'))
cfg

{'portfolio_id': 'JW_SP100',
 'index': 'S&P100',
 'opt_kwargs': {'start_date': '2020-01-01',
  'end_date': '2022-05-27',
  'lambda_risk': 5.0,
  'leverage_limit': 2,
  'max_weights': 0.5,
  'min_weights': -0.5,
  'adv_limit': 0.05,
  'half_spread': 0.0001,
  'borrow_costs': 0.001}}

In [7]:
# get universe
univ = query_universe(cfg['index']); display(univ)
tickers = univ.Symbol.tolist()

Symbol                      Name                  Sector
0     AAPL                     Apple  Information Technology
1     ABBV                    AbbVie             Health Care
2      ABT                    Abbott             Health Care
3      ACN                 Accenture  Information Technology
4     ADBE                     Adobe  Information Technology
..     ...                       ...                     ...
96      VZ                   Verizon  Communication Services
97     WBA  Walgreens Boots Alliance        Consumer Staples
98     WFC               Wells Fargo              Financials
99     WMT                   Walmart        Consumer Staples
100    XOM                ExxonMobil                  Energy

[101 rows x 3 columns]

In [9]:
# get holdings
positions_loader = PositionsLoader('url://whatever.abc.com', cfg['portfolio_id'])
holdings = positions_loader.query(tickers, t=run_date)
holdings

INFO:root:connected to position database url://whatever.abc.com 
INFO:root:PositionsLoader loaded positions for JW_SP100 on 2022-05-26 00:00:00


AAPL    6.414832e+05
ABBV    4.304072e+06
ABT     1.392705e+05
ACN     9.165618e+05
ADBE    1.862251e+06
            ...     
WBA     1.460017e+06
WFC     1.229980e+06
WMT     4.388362e+05
XOM     1.637707e+06
cash    9.347985e+05
Name: JW_SP100, Length: 102, dtype: float64

In [11]:
# get signals
optimizer = Optimizer(tickers, **cfg['opt_kwargs'])
signals = optimizer.return_forecast
signals

INFO:root:built signals from 2020-01-01 to 2022-05-27
INFO:root:built risk model from 2020-01-01 to 2022-05-27


AAPL      ABBV       ABT       ACN      ADBE       AIG  \
Date                                                                     
2020-12-24  0.002816  0.001075  0.001254  0.001210  0.002122 -0.000075   
2020-12-28  0.002959  0.001082  0.001233  0.001247  0.002115 -0.000107   
2020-12-29  0.002814  0.001085  0.001249  0.001226  0.002084 -0.000131   
2020-12-30  0.002819  0.001145  0.001302  0.001229  0.002078 -0.000061   
2020-12-31  0.002756  0.001185  0.001319  0.001312  0.002077 -0.000028   
...              ...       ...       ...       ...       ...       ...   
2022-05-20  0.000497  0.001354 -0.000003  0.000048 -0.000668  0.000657   
2022-05-23  0.000659  0.001270  0.000116  0.000174 -0.000606  0.000707   
2022-05-24  0.000631  0.001382  0.000109  0.000171 -0.000619  0.000573   
2022-05-25  0.000657  0.001427  0.000055  0.000146 -0.000629  0.000574   
2022-05-26  0.000761  0.001426  0.000487  0.000334 -0.000499  0.000595   

                AMGN       AMT      AMZN      AVGO  ...       UNP       UPS  \
Date                                                ...                       
2020-12-24  0.000086  0.000259  0.002458  0.001962  ...  0.000910  0.002009   
2020-12-28  0.000099  0.000304  0.002598  0.001966  ...  0.000954  0.001990   
2020-12-29  0.000172  0.000316  0.002536  0.001859  ...  0.000898  0.001945   
2020-12-30  0.000205  0.000311  0.002541  0.002015  ...  0.000957  0.001881   
2020-12-31  0.000223  0.000387  0.002446  0.002049  ...  0.001034  0.001951   
...              ...       ...       ...       ...  ...       ...       ...   
2022-05-20  0.000300  0.000040 -0.001367  0.000969  ...  0.000017 -0.000581   
2022-05-23  0.000382  0.000107 -0.001376  0.000837  ...  0.000044 -0.000547   
2022-05-24  0.000482  0.000258 -0.001461  0.000758  ...  0.000028 -0.000534   
2022-05-25  0.000455  0.000264 -0.001350  0.000775  ...  0.000019 -0.000574   
2022-05-26  0.000529  0.000130 -0.001183  0.000952  ...  0.000085 -0.000446   

                 USB         V        VZ       WBA       WFC       WMT  \
Date                                                                     
2020-12-24 -0.000151  0.000807  0.000120 -0.000948 -0.001447  0.001016   
2020-12-28 -0.000136  0.000882  0.000130 -0.000944 -0.001435  0.001064   
2020-12-29 -0.000175  0.000846  0.000141 -0.000977 -0.001451  0.001035   
2020-12-30 -0.000090  0.000953  0.000138 -0.000984 -0.001430  0.001067   
2020-12-31  0.000003  0.000968  0.000189 -0.000964 -0.001349  0.001074   
...              ...       ...       ...       ...       ...       ...   
2022-05-20 -0.000500 -0.000365 -0.000283 -0.000804 -0.000101 -0.000556   
2022-05-23 -0.000381 -0.000160 -0.000263 -0.000527  0.000078 -0.000437   
2022-05-24 -0.000425 -0.000251 -0.000177 -0.000613 -0.000001 -0.000374   
2022-05-25 -0.000416 -0.000235 -0.000147 -0.000548  0.000079 -0.000408   
2022-05-26 -0.000356 -0.000131 -0.000159 -0.000507  0.000167 -0.000312   

                 XOM  cash  
Date                        
2020-12-24 -0.001203   0.0  
2020-12-28 -0.001189   0.0  
2020-12-29 -0.001299   0.0  
2020-12-30 -0.001235   0.0  
2020-12-31 -0.001302   0.0  
...              ...   ...  
2022-05-20  0.002206   0.0  
2022-05-23  0.002248   0.0  
2022-05-24  0.002295   0.0  
2022-05-25  0.002389   0.0  
2022-05-26  0.002260   0.0  

[358 rows x 102 columns]

In [62]:
# construct TE and generate orders
te = TradeEngine(cfg['portfolio_id'], tickers, optimizer)
orders = te.get_orders(holdings, t=run_date)
orders.sample(10)

INFO:root:initialized Trade Engine


symbol  quantity security_type       side order_type  algo broker  \
79   QCOM   -5300.0        EQUITY       SELL        MKT  VWAP    JPM   
39    FDX    -300.0        EQUITY       SELL        MKT  VWAP    JPM   
11     BA -276700.0        EQUITY  SHORTSELL        MKT  VWAP    JPM   
43     GM  -32800.0        EQUITY  SHORTSELL        MKT  VWAP    JPM   
80    RTX   -7700.0        EQUITY       SELL        MKT  VWAP    JPM   
44   GOOG    -200.0        EQUITY       SELL        MKT  VWAP    JPM   
53    KHC  -35900.0        EQUITY       SELL        MKT  VWAP    JPM   
24    COP  432200.0        EQUITY        BUY        MKT  VWAP    JPM   
89   TSLA   23900.0        EQUITY        BUY        MKT  VWAP    JPM   
92    UNP   -4300.0        EQUITY       SELL        MKT  VWAP    JPM   

   portfolio_id             order_id             batch_id  
79     JW_SP100  -747988733205410648 -7688841925512768270  
39     JW_SP100  7802889108425999559 -7688841925512768270  
11     JW_SP100 -1706919581496188002 -7688841925512768270  
43     JW_SP100 -5252874350418682054 -7688841925512768270  
80     JW_SP100 -4501502196227486411 -7688841925512768270  
44     JW_SP100  4268786761680794757 -7688841925512768270  
53     JW_SP100  6624715386573677995 -7688841925512768270  
24     JW_SP100  1557401284403525694 -7688841925512768270  
89     JW_SP100 -4338393533894819557 -7688841925512768270  
92     JW_SP100 -5662526934417984414 -7688841925512768270

In [20]:
# back-test
returns = query_ret(tickers, cfg['opt_kwargs']['start_date'], cfg['opt_kwargs']['end_date'])
market_sim = cp.MarketSimulator(returns, [], cash_key='cash') 

result = market_sim.run_backtest(holdings, start_time="2021-01-01", end_time="2022-05-26", policy=optimizer)
result.summary()

Number of periods                               353
Initial timestamp               2021-01-04 00:00:00
Final timestamp                 2022-05-26 00:00:00
Portfolio return (%)                         54.202
Excess return (%)                            54.202
Excess risk (%)                              24.150
Sharpe ratio                                  2.248
Max. drawdown                                14.024
Turnover (%)                              3,900.994
Average policy time (sec)                     0.090
Average simulator time (sec)                  0.001


In [21]:
result.v.plot()

In [23]:
result.h.drop('cash', axis=1).plot()